# Elo Merchant Categories
### Competition on Kaggle
## Outlier Detection: Bag of Catboost Classifiers
### 7-1-2019

In [1]:
## Variables specific for competition

ID = 'card_id'                                            
TARGET = 'target'    

RAW_DIRECTORY = 'C:/Users/judit/Documents/learning/kaggle/Elo_201812/rawdata/'  
DIRECTORY = 'C:/Users/judit/Documents/learning/kaggle/Elo_201812/data/'
HIST_TRANS_FILE = RAW_DIRECTORY + 'historical_transactions.csv'
MERCHANTS_FILE = RAW_DIRECTORY + 'merchants.csv'
NEW_MERCH_TRANS_FILE = RAW_DIRECTORY + 'new_merchant_transactions.csv'
TRAIN_FILE = RAW_DIRECTORY + 'train.csv'    
TEST_FILE = RAW_DIRECTORY +'test.csv'
SAMPLE_SUBMISSION_FILE = RAW_DIRECTORY + 'sample_submission.csv'

SUBMISSION_DIRECTORY = 'C:/Users/judit/Documents/learning/kaggle/Elo_201812/submissions/'

In [2]:
## Variables specific for notebook
NUM = 0
SUBMIT_FILENAME = SUBMISSION_DIRECTORY + 'submit_190104_'

HIST_AGG_FILE_1 = DIRECTORY + 'hist_agg_20.pkl'        # only authorized, domestic, last 3 months
HIST_AGG_FILE_2 = DIRECTORY + 'hist_agg_28.pkl'        # only authorized, non-domestic, last 3 months
NEW_AGG_FILE_1 = DIRECTORY + 'new_agg_3.pkl'           # only authorized, domestic, whole period
NEW_AGG_FILE_2 = DIRECTORY + 'new_agg_5.pkl'           # only authorized, non-domestic, whole period

In [3]:
from catboost import CatBoostRegressor, CatBoostClassifier
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.utils import resample
from sklearn.metrics import mean_squared_error, accuracy_score, log_loss, confusion_matrix
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import pickle
import random
random.seed(1)

In [4]:
## Useful functions
def reduce_mem_usage(df, verbose = True):
    numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
    start_mem = df.memory_usage().sum() / 1024**2
    if verbose: print('Starting memory usage: {:5.2f} MB'.format(start_mem))

    for col in df.columns:
        col_type = df[col].dtypes
        if col_type in numerics:
            c_min = df[col].min()
            c_max = df[col].max()
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)  
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)    
    end_mem = df.memory_usage().sum() / 1024**2
    if verbose: print('Reduced memory usage: {:5.2f} MB ({:.1f}% reduction)'.format(end_mem, 100 * (start_mem - end_mem\
                                                                                                   ) / start_mem))
    return df

def mode(series):
    if len(series.mode()) > 0:
        return series.mode().iloc[0]
    else:
        return np.nan

def label_encoder(train_df, test_df = None, valid_df = None, localtest_df = None,
                  prefix = '_labelenc_', suffix = '',
                  target = 'is_outlier',
                  cols_and_encodings = {'feature_1' : ['mean', 'median'],
                                         'feature_2' : [mode]}):
    '''
    Calculates label encodings based on train_df.
    Can be used both for classification and regression problems.
    
    cols_and_encodings is a dictionary. 
    Keys: features that we want to encode (usually categorical features with only a few possible values).
    Values : list of aggregation functions which will be applied on target values.
    '''
    for col, enc_list in cols_and_encodings.items():
        agg_df = train_df.groupby(col).agg({target : enc_list})
        agg_df.columns = [col + prefix + '_'.join(colname).strip() + suffix for colname in agg_df.columns.values]  
        agg_df.reset_index(inplace = True)
        train_df = train_df.merge(agg_df, how = 'left', on = col)
        if test_df:
            test_df = test_df.merge(agg_df, how = 'left', on = col)
        if valid_df:
            valid_df = valid_df.merge(agg_df, how = 'left', on = col)
        if localtest_df:
            localtest_df = localtest_df.merge(agg_df, how = 'left', on = col)

    return train_df, test_df, valid_df, localtest_df

In [5]:
hist_agg_1 = pd.read_pickle(HIST_AGG_FILE_1)
hist_agg_2 = pd.read_pickle(HIST_AGG_FILE_2)
new_agg_1 = pd.read_pickle(NEW_AGG_FILE_1)
new_agg_2 = pd.read_pickle(NEW_AGG_FILE_2)
merch = pd.read_csv(MERCHANTS_FILE)
train = pd.read_csv(TRAIN_FILE, parse_dates = ["first_active_month"])
merch = pd.read_csv(MERCHANTS_FILE)

params = {'learning_rate' : 0.99,
          'iterations' : 3000,
          'depth' : 10,
          'l2_leaf_reg' : 1000}

train.head()

first_active_month          card_id  feature_1  feature_2  feature_3  \
0         2017-06-01  C_ID_92a2005557          5          2          1   
1         2017-01-01  C_ID_3d0044924f          4          1          0   
2         2016-08-01  C_ID_d639edf6cd          2          2          0   
3         2017-09-01  C_ID_186d6a6901          4          3          0   
4         2017-11-01  C_ID_cdbd2c0db2          1          3          0   

     target  
0 -0.820283  
1  0.392913  
2  0.688056  
3  0.142495  
4 -0.159749

In [6]:
categorical_features = ['first_active_month',
                        'card_id',
                        'feature_1',
                        'feature_2',
                        'feature_3',
                        'hist_city_id_mode_auth_dom_lag2m',
                        'hist_category_3_mode_auth_dom_lag2m',
                        'hist_merchant_category_id_mode_auth_dom_lag2m',
                        'hist_merchant_id_mode_auth_dom_lag2m',
                        'hist_category_2_mode_auth_dom_lag2m',
                        'hist_state_id_mode_auth_dom_lag2m',
                        'hist_subsector_id_mode_auth_dom_lag2m',
                        'hist_city_id_mode_auth_nondom_lag2m',
                        'hist_category_3_mode_auth_nondom_lag2m',
                        'hist_merchant_category_id_mode_auth_nondom_lag2m',
                        'hist_merchant_id_mode_auth_nondom_lag2m',
                        'hist_category_2_mode_auth_nondom_lag2m',
                        'hist_state_id_mode_auth_nondom_lag2m',
                        'hist_subsector_id_mode_auth_nondom_lag2m',
                        'new_city_id_mode_dom_all',
                        'new_category_3_mode_dom_all',
                        'new_merchant_category_id_mode_dom_all',
                        'new_merchant_id_mode_dom_all',
                        'new_category_2_mode_dom_all',
                        'new_state_id_mode_dom_all',
                        'new_subsector_id_mode_dom_all',
                        'new_city_id_mode_nondom_all',
                        'new_category_3_mode_nondom_all',
                        'new_merchant_category_id_mode_nondom_all',
                        'new_merchant_id_mode_nondom_all',
                        'new_category_2_mode_nondom_all',
                        'new_state_id_mode_nondom_all',
                        'new_subsector_id_mode_nondom_all',
                        'merchant_group_id_hist_merchant_id_mode_auth_dom_lag2m',
                        'merchant_category_id_hist_merchant_id_mode_auth_dom_lag2m',
                        'subsector_id_hist_merchant_id_mode_auth_dom_lag2m',
                        'city_id_hist_merchant_id_mode_auth_dom_lag2m',
                        'state_id_hist_merchant_id_mode_auth_dom_lag2m',
                        'category_2_hist_merchant_id_mode_auth_dom_lag2m',
                        'merchant_group_id_hist_merchant_id_mode_auth_nondom_lag2m',
                        'merchant_category_id_hist_merchant_id_mode_auth_nondom_lag2m',
                        'subsector_id_hist_merchant_id_mode_auth_nondom_lag2m',
                        'city_id_hist_merchant_id_mode_auth_nondom_lag2m',
                        'state_id_hist_merchant_id_mode_auth_nondom_lag2m',
                        'category_2_hist_merchant_id_mode_auth_nondom_lag2m',
                        'merchant_group_id_new_merchant_id_mode_dom_all',
                        'merchant_category_id_new_merchant_id_mode_dom_all',
                        'subsector_id_new_merchant_id_mode_dom_all',
                        'city_id_new_merchant_id_mode_dom_all',
                        'state_id_new_merchant_id_mode_dom_all',
                        'category_2_new_merchant_id_mode_dom_all',
                        'merchant_group_id_new_merchant_id_mode_nondom_all',
                        'merchant_category_id_new_merchant_id_mode_nondom_all',
                        'subsector_id_new_merchant_id_mode_nondom_all',
                        'city_id_new_merchant_id_mode_nondom_all',
                        'state_id_new_merchant_id_mode_nondom_all',
                        'category_2_new_merchant_id_mode_nondom_all']

In [7]:
def data_transformations_and_merges():
    global train, merch
    # define feature 'is_outlier'
    train['is_outlier'] = train['target'].apply(lambda x : x < -30)
    train['is_outlier'] = train['is_outlier'].apply(lambda x : int(x))
    # card_id is a hexadecimal number. Convert it into decimal.
    train['card_id'] = train['card_id'].apply(lambda s : int(s[5:], 16))
    train = reduce_mem_usage(df = train, verbose = True)
    
    # merchant_id is a hexadecimal number. Convert it into decimal.
    merch['merchant_id'] = merch['merchant_id'].apply(lambda s : int(s[5:], 16))
    # convert categorical features into numerical ones
    merch['category_1'] = merch['category_1'].apply(lambda x : 1 if x == 'Y' else 0 if x == 'N' else np.nan)
    merch['most_recent_sales_range'] = merch['most_recent_sales_range'].apply(lambda x : 1 if x == 'A' else
                                                                                         2 if x == 'B' else
                                                                                         3 if x == 'C' else
                                                                                         4 if x == 'D' else
                                                                                         5 if x == 'E' else
                                                                                         np.nan)
    merch['most_recent_purchases_range'] = merch['most_recent_purchases_range'].apply(lambda x : 1 if x == 'A' else
                                                                                                 2 if x == 'B' else
                                                                                                 3 if x == 'C' else
                                                                                                 4 if x == 'D' else
                                                                                                 5 if x == 'E' else
                                                                                                 np.nan)
    merch['category_4'] = merch['category_4'].apply(lambda x : 1 if x == 'Y' else 0 if x == 'N' else np.nan)
    merch = reduce_mem_usage(df = merch, verbose = True)
    
    # merges
    df = train.merge(hist_agg_1, how = 'left', on = 'card_id')
    df = df.merge(hist_agg_2, how = 'left', on = 'card_id')
    df = df.merge(new_agg_1, how = 'left', on = 'card_id')
    df = df.merge(new_agg_2, how = 'left', on = 'card_id')
    df = df.merge(merch, how = 'left', left_on = 'hist_merchant_id_mode_auth_dom_lag2m', right_on = 'merchant_id',
                  suffixes = ('', '_hist_merchant_id_mode_auth_dom_lag2m'))
    df = df.merge(merch, how = 'left', left_on = 'hist_merchant_id_mode_auth_nondom_lag2m', right_on = 'merchant_id',
                  suffixes = ('', '_hist_merchant_id_mode_auth_nondom_lag2m'))
    df = df.merge(merch, how = 'left', left_on = 'new_merchant_id_mode_dom_all', right_on = 'merchant_id',
                  suffixes = ('', '_new_merchant_id_mode_dom_all'))
    df = df.merge(merch, how = 'left', left_on = 'new_merchant_id_mode_nondom_all', right_on = 'merchant_id',
                  suffixes = ('', '_new_merchant_id_mode_nondom_all'))
    for colname in merch.columns:
        df.rename(columns = {colname: colname + '_hist_merchant_id_mode_auth_dom_lag2m'}, inplace = True)
    df.drop(['merchant_id_hist_merchant_id_mode_auth_dom_lag2m',
             'merchant_id_hist_merchant_id_mode_auth_nondom_lag2m',
             'merchant_id_new_merchant_id_mode_dom_all',
             'merchant_id_new_merchant_id_mode_nondom_all'], inplace = True, axis = 1)
    
    # Prepair data for CatBoostClassifier
    # impute string for missing categorical values (catboost can't handle np.nan in categorical features)
    df[categorical_features] = df[categorical_features].fillna('nan')
    
    for col in categorical_features:
        df[col] = df[col].astype('category').cat.codes
    
    return df

In [8]:
df = data_transformations_and_merges()

Starting memory usage: 10.78 MB
Reduced memory usage:  4.24 MB (60.7% reduction)
Starting memory usage: 56.18 MB
Reduced memory usage: 21.39 MB (61.9% reduction)


### Split into train and localtest

In [9]:
# create training and local test sets
X = df.drop(['target'], axis = 1)
y = df.target.copy()

# split into training set (80%) and local test set (20%)
X_train, X_localtest, y_train, y_localtest = train_test_split(X, y, train_size = 0.8, random_state = 1,
                                                              stratify = X[['feature_1', 'feature_2', 'feature_3', 
                                                                            'is_outlier']])

C:\ProgramData\Anaconda3\envs\gbms\lib\site-packages\sklearn\model_selection\_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


In [10]:
X_train.shape, X_train[X_train['is_outlier'] == 1].shape

((161533, 488), (1765, 488))

In [11]:
y_localtest_label = X_localtest.is_outlier.copy()
X_localtest = X_localtest.drop('is_outlier', axis = 1)

### Create 32 small training sets  
Each of these training sets will include 5000 rows of majority class and 5000 rows of minority class (upsampled).

In [12]:
def create_small_training_sets(df = X_train, col = 'is_outlier', seed = 1, majority_label = 0, minority_label = 1,
                               majority_cnt = 5000, minority_cnt = 5000):
    random.seed(seed)
    
    # list of small training sets
    training_sets = []
    
    # Separate majority and minority classes
    df_majority = df[df[col] == majority_label]
    df_minority = df[df[col] == minority_label]
    
    # Shuffle majority class
    df_majority = df_majority.sample(frac = 1, random_state = seed).reset_index(drop = True)
    
    # Count of iterations through df_majority
    cnt_iter = df_majority.shape[0] // majority_cnt
    
    for idx in range(cnt_iter):
        # Rows from the majority class
        df_majority_subsample = df_majority.iloc[idx * majority_cnt : (idx + 1) * majority_cnt, :]
        # Upsample minority class
        df_minority_upsampled = resample(df_minority, replace = True, n_samples = minority_cnt, random_state = seed + idx)
    
        # Combine majority class with upsampled minority class
        df_resampled = pd.concat([df_majority_subsample, df_minority_upsampled])
        
        # Shuffle
        df_resampled = df_resampled.sample(frac = 1, random_state = seed + idx).reset_index(drop = True)
        
        df_resampled_label = df_resampled.is_outlier.copy()
        df_resampled = df_resampled.drop('is_outlier', axis = 1)

        
        training_sets.append((df_resampled, df_resampled_label))
    
    if df_majority.shape[0] % majority_cnt != 0:
        # Rows from the majority class
        df_majority_subsample = df_majority.iloc[majority_cnt * cnt_iter : , :]
        # Missing rows from the majority class
        missing_cnt = majority_cnt - df_majority_subsample.shape[0]
        # Sample the missing rows
        df_majority_upsampled = resample(df_majority, replace = True, n_samples = missing_cnt, random_state = seed)
        
         # Upsample minority class
        df_minority_upsampled = resample(df_minority, replace = True, n_samples = minority_cnt, random_state = seed + cnt_iter)
    
        # Combine majority class with upsampled minority class
        df_resampled = pd.concat([df_majority_subsample, df_majority_upsampled, df_minority_upsampled])
        
        # Shuffle
        df_resampled = df_resampled.sample(frac = 1, random_state = seed + cnt_iter).reset_index(drop = True)
        
        df_resampled_label = df_resampled.is_outlier.copy()
        df_resampled = df_resampled.drop('is_outlier', axis = 1)
        
        training_sets.append((df_resampled, df_resampled_label))
    
    return training_sets

In [13]:
training_sets = create_small_training_sets()

In [14]:
# head of the first training set
training_sets[0][0].head()

first_active_month  card_id  feature_1  feature_2  feature_3  \
0                  65    94219          1          0          0   
1                  69    90372          2          2          1   
2                  68    50764          1          0          0   
3                  60   166060          2          0          1   
4                  70     6395          4          1          1   

   hist_authorized_flag_sum_auth_dom_lag2m  \
0                                      6.0   
1                                     16.0   
2                                      NaN   
3                                     14.0   
4                                     34.0   

   hist_authorized_flag_mean_auth_dom_lag2m  \
0                                       1.0   
1                                       1.0   
2                                       NaN   
3                                       1.0   
4                                       1.0   

   hist_city_id_nunique_auth_dom_lag2m  hist_city_id_mode_auth_dom_lag2m  \
0                                  3.0                                77   
1                                  2.0                               283   
2                                  NaN                               306   
3                                  3.0                               296   
4                                  2.0                                16   

   hist_city_id_nancnt_auth_dom_lag2m  \
0                                 0.0   
1                                 0.0   
2                                 NaN   
3                                 0.0   
4                                 0.0   

                      ...                      \
0                     ...                       
1                     ...                       
2                     ...                       
3                     ...                       
4                     ...                       

   avg_sales_lag6_new_merchant_id_mode_nondom_all  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

   avg_purchases_lag6_new_merchant_id_mode_nondom_all  \
0                                                NaN    
1                                                NaN    
2                                                NaN    
3                                                NaN    
4                                                NaN    

   active_months_lag6_new_merchant_id_mode_nondom_all  \
0                                                NaN    
1                                                NaN    
2                                                NaN    
3                                                NaN    
4                                                NaN    

   avg_sales_lag12_new_merchant_id_mode_nondom_all  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

   avg_purchases_lag12_new_merchant_id_mode_nondom_all  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

   active_months_lag12_new_merchant_id_mode_nondom_all  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

   category_4

In [15]:
# labelst of the first training set
training_sets[0][1][:10]

0    1
1    0
2    0
3    0
4    1
5    1
6    0
7    0
8    0
9    1
Name: is_outlier, dtype: int8

In [16]:
# head of the last training set
training_sets[-1][0].head()

first_active_month  card_id  feature_1  feature_2  feature_3  \
0                  31      585          2          2          1   
1                  70   118392          1          0          0   
2                  55    14432          2          2          1   
3                  62    32342          1          0          0   
4                  58    93467          1          1          0   

   hist_authorized_flag_sum_auth_dom_lag2m  \
0                                     12.0   
1                                     28.0   
2                                      3.0   
3                                      1.0   
4                                     50.0   

   hist_authorized_flag_mean_auth_dom_lag2m  \
0                                       1.0   
1                                       1.0   
2                                       1.0   
3                                       1.0   
4                                       1.0   

   hist_city_id_nunique_auth_dom_lag2m  hist_city_id_mode_auth_dom_lag2m  \
0                                  5.0                               137   
1                                  2.0                               183   
2                                  1.0                               274   
3                                  1.0                                 3   
4                                  5.0                                57   

   hist_city_id_nancnt_auth_dom_lag2m  \
0                                 0.0   
1                                 0.0   
2                                 0.0   
3                                 0.0   
4                                 0.0   

                      ...                      \
0                     ...                       
1                     ...                       
2                     ...                       
3                     ...                       
4                     ...                       

   avg_sales_lag6_new_merchant_id_mode_nondom_all  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

   avg_purchases_lag6_new_merchant_id_mode_nondom_all  \
0                                                NaN    
1                                                NaN    
2                                                NaN    
3                                                NaN    
4                                                NaN    

   active_months_lag6_new_merchant_id_mode_nondom_all  \
0                                                NaN    
1                                                NaN    
2                                                NaN    
3                                                NaN    
4                                                NaN    

   avg_sales_lag12_new_merchant_id_mode_nondom_all  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

   avg_purchases_lag12_new_merchant_id_mode_nondom_all  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

   active_months_lag12_new_merchant_id_mode_nondom_all  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

   category_4

In [17]:
# labelst of the last training set
training_sets[-1][1][:10]

0    1
1    0
2    0
3    1
4    1
5    0
6    0
7    0
8    1
9    1
Name: is_outlier, dtype: int8

In [18]:
training_sets[-1][0].shape

(10000, 487)

### Step 1: Classification to find outliers

#### Train series of classifications on each small training sets

In [19]:
ignored_features = ['first_active_month', 'card_id']
for training_set, training_label in training_sets:
    for col in categorical_features:
        training_set[col] = training_set[col].astype('category').cat.codes
categorical_features_indices = [training_sets[0][0].columns.get_loc(i) for i in categorical_features]
ignored_features_indices = [training_sets[0][0].columns.get_loc(i) for i in ignored_features]

In [20]:
def train_catboost_classifier(params,
                              train_set,
                              train_label,
                              categorical_features = categorical_features,
                              ignored_features = ignored_features,
                              n_jobs = 8,
                              seed = 1):
    random.seed(seed)
    
    for col in categorical_features:
        train_set[col] = train_set[col].astype('category').cat.codes
    categorical_features_indices = [train_set.columns.get_loc(i) for i in categorical_features]
    ignored_features_indices = [train_set.columns.get_loc(i) for i in ignored_features]
    
    model = CatBoostClassifier(**params, ignored_features = ignored_features_indices, random_seed = seed, thread_count = n_jobs)
    model.fit(train_set, train_label, cat_features = categorical_features_indices)
    
    return model

In [21]:
def train_list_of_classifiers(params,
                              training_sets = training_sets,
                              categorical_features = categorical_features,
                              ignored_features = ignored_features,
                              n_jobs = 8,
                              seed = 1):
    models = []
    idx = 0
    for train_set, train_label in training_sets:
        print('Training model', idx)
        model = train_catboost_classifier(params, train_set, train_label, categorical_features = categorical_features,
                                          ignored_features = ignored_features, n_jobs = n_jobs, seed = seed)
        models.append(model)
        pickle.dump(models, open(DIRECTORY + 'catboostclassifiers_12_notebook.p',   'wb'))
        idx += 1
    
    return models

In [22]:
def make_list_of_predictions(models_list, test_set):
    predictions_class = []
    predictions_proba = []
    idx = 0
    for model in models_list:
        print('Predict for model', idx)
        prediction_class = model.predict(test_set)
        prediction_proba = model.predict_proba(test_set)
        predictions_class.append(prediction_class)
        predictions_proba.append(predictions_proba)
        idx += 1
    return predictions_class, predictions_proba

In [23]:
models = train_list_of_classifiers(params = params)

predictions_class, predictions_proba = make_list_of_predictions(models_list = models, test_set = X_localtest)
pickle.dump(predictions_class, open(DIRECTORY + 'predictions_class_12_notebook_1.p', 'wb'))
pickle.dump(predictions_proba, open(DIRECTORY + 'predictions_proba_12_notebook_1.p', 'wb'))

Training model 0
0:	learn: 0.5245478	total: 251ms	remaining: 12m 34s
1:	learn: 0.4129778	total: 399ms	remaining: 9m 57s
2:	learn: 0.3556255	total: 2.3s	remaining: 38m 17s
3:	learn: 0.3438803	total: 3.16s	remaining: 39m 27s
4:	learn: 0.3389504	total: 5.21s	remaining: 51m 58s
5:	learn: 0.3344255	total: 7.4s	remaining: 1h 1m 32s
6:	learn: 0.3289824	total: 7.45s	remaining: 53m 4s
7:	learn: 0.3281567	total: 7.91s	remaining: 49m 17s
8:	learn: 0.3261618	total: 8.01s	remaining: 44m 21s
9:	learn: 0.3212463	total: 10.1s	remaining: 50m 7s
10:	learn: 0.3156916	total: 12s	remaining: 54m 13s
11:	learn: 0.3129262	total: 13.8s	remaining: 57m 20s
12:	learn: 0.3113882	total: 15.7s	remaining: 1h 15s
13:	learn: 0.3085024	total: 17.4s	remaining: 1h 1m 53s
14:	learn: 0.3064388	total: 19.2s	remaining: 1h 3m 38s
15:	learn: 0.3035051	total: 20.9s	remaining: 1h 5m
16:	learn: 0.3014887	total: 22.6s	remaining: 1h 6m 3s
17:	learn: 0.2994826	total: 24.2s	remaining: 1h 6m 56s
18:	learn: 0.2968559	total: 26.2s	remain

146:	learn: 0.1709158	total: 4m 35s	remaining: 1h 29m 14s
147:	learn: 0.1703920	total: 4m 37s	remaining: 1h 29m 14s
148:	learn: 0.1695112	total: 4m 40s	remaining: 1h 29m 21s
149:	learn: 0.1690269	total: 4m 42s	remaining: 1h 29m 26s
150:	learn: 0.1685995	total: 4m 45s	remaining: 1h 29m 41s
151:	learn: 0.1683641	total: 4m 47s	remaining: 1h 29m 47s
152:	learn: 0.1680991	total: 4m 49s	remaining: 1h 29m 51s
153:	learn: 0.1674698	total: 4m 51s	remaining: 1h 29m 55s
154:	learn: 0.1668333	total: 4m 54s	remaining: 1h 30m 5s
155:	learn: 0.1662872	total: 4m 56s	remaining: 1h 30m 14s
156:	learn: 0.1660900	total: 4m 59s	remaining: 1h 30m 16s
157:	learn: 0.1657390	total: 5m 1s	remaining: 1h 30m 24s
158:	learn: 0.1653868	total: 5m 3s	remaining: 1h 30m 28s
159:	learn: 0.1648878	total: 5m 6s	remaining: 1h 30m 33s
160:	learn: 0.1645217	total: 5m 8s	remaining: 1h 30m 36s
161:	learn: 0.1640754	total: 5m 10s	remaining: 1h 30m 42s
162:	learn: 0.1636701	total: 5m 12s	remaining: 1h 30m 45s
163:	learn: 0.16343

289:	learn: 0.1169620	total: 9m 15s	remaining: 1h 26m 28s
290:	learn: 0.1166380	total: 9m 17s	remaining: 1h 26m 25s
291:	learn: 0.1164047	total: 9m 18s	remaining: 1h 26m 22s
292:	learn: 0.1161890	total: 9m 20s	remaining: 1h 26m 18s
293:	learn: 0.1160527	total: 9m 22s	remaining: 1h 26m 17s
294:	learn: 0.1158309	total: 9m 24s	remaining: 1h 26m 16s
295:	learn: 0.1155964	total: 9m 26s	remaining: 1h 26m 15s
296:	learn: 0.1134160	total: 9m 28s	remaining: 1h 26m 15s
297:	learn: 0.1129807	total: 9m 30s	remaining: 1h 26m 13s
298:	learn: 0.1127921	total: 9m 32s	remaining: 1h 26m 11s
299:	learn: 0.1125093	total: 9m 34s	remaining: 1h 26m 10s
300:	learn: 0.1122026	total: 9m 36s	remaining: 1h 26m 9s
301:	learn: 0.1117198	total: 9m 38s	remaining: 1h 26m 9s
302:	learn: 0.1114545	total: 9m 40s	remaining: 1h 26m 10s
303:	learn: 0.1110518	total: 9m 42s	remaining: 1h 26m 7s
304:	learn: 0.1107928	total: 9m 44s	remaining: 1h 26m 7s
305:	learn: 0.1106157	total: 9m 46s	remaining: 1h 26m 4s
306:	learn: 0.11040

430:	learn: 0.0900772	total: 14m 7s	remaining: 1h 24m 12s
431:	learn: 0.0900476	total: 14m 9s	remaining: 1h 24m 11s
432:	learn: 0.0900157	total: 14m 11s	remaining: 1h 24m 9s
433:	learn: 0.0900008	total: 14m 13s	remaining: 1h 24m 8s
434:	learn: 0.0899519	total: 14m 16s	remaining: 1h 24m 8s
435:	learn: 0.0899447	total: 14m 18s	remaining: 1h 24m 8s
436:	learn: 0.0896938	total: 14m 20s	remaining: 1h 24m 7s
437:	learn: 0.0895035	total: 14m 22s	remaining: 1h 24m 7s
438:	learn: 0.0892813	total: 14m 25s	remaining: 1h 24m 6s
439:	learn: 0.0891812	total: 14m 27s	remaining: 1h 24m 5s
440:	learn: 0.0891176	total: 14m 29s	remaining: 1h 24m 4s
441:	learn: 0.0890723	total: 14m 31s	remaining: 1h 24m 2s
442:	learn: 0.0889908	total: 14m 33s	remaining: 1h 24m
443:	learn: 0.0889645	total: 14m 35s	remaining: 1h 23m 58s
444:	learn: 0.0889298	total: 14m 37s	remaining: 1h 23m 58s
445:	learn: 0.0887296	total: 14m 39s	remaining: 1h 23m 58s
446:	learn: 0.0886611	total: 14m 41s	remaining: 1h 23m 57s
447:	learn: 0

571:	learn: 0.0753439	total: 19m 16s	remaining: 1h 21m 48s
572:	learn: 0.0752700	total: 19m 18s	remaining: 1h 21m 47s
573:	learn: 0.0751484	total: 19m 20s	remaining: 1h 21m 46s
574:	learn: 0.0750022	total: 19m 23s	remaining: 1h 21m 45s
575:	learn: 0.0749238	total: 19m 25s	remaining: 1h 21m 43s
576:	learn: 0.0747628	total: 19m 27s	remaining: 1h 21m 42s
577:	learn: 0.0747420	total: 19m 29s	remaining: 1h 21m 40s
578:	learn: 0.0746357	total: 19m 32s	remaining: 1h 21m 41s
579:	learn: 0.0745226	total: 19m 34s	remaining: 1h 21m 39s
580:	learn: 0.0743825	total: 19m 36s	remaining: 1h 21m 38s
581:	learn: 0.0743437	total: 19m 38s	remaining: 1h 21m 37s
582:	learn: 0.0742575	total: 19m 40s	remaining: 1h 21m 36s
583:	learn: 0.0741719	total: 19m 43s	remaining: 1h 21m 34s
584:	learn: 0.0741317	total: 19m 45s	remaining: 1h 21m 32s
585:	learn: 0.0740427	total: 19m 47s	remaining: 1h 21m 31s
586:	learn: 0.0740363	total: 19m 49s	remaining: 1h 21m 29s
587:	learn: 0.0739125	total: 19m 51s	remaining: 1h 21m 2

...

2446:	learn: 0.0241053	total: 2h 5m 3s	remaining: 28m 15s
2447:	learn: 0.0240929	total: 2h 5m 5s	remaining: 28m 12s
2448:	learn: 0.0240889	total: 2h 5m 8s	remaining: 28m 9s
2449:	learn: 0.0240860	total: 2h 5m 11s	remaining: 28m 6s
2450:	learn: 0.0240624	total: 2h 5m 14s	remaining: 28m 3s
2451:	learn: 0.0240508	total: 2h 5m 16s	remaining: 27m 59s
2452:	learn: 0.0240486	total: 2h 5m 19s	remaining: 27m 56s
2453:	learn: 0.0240370	total: 2h 5m 22s	remaining: 27m 53s
2454:	learn: 0.0240354	total: 2h 5m 26s	remaining: 27m 50s
2455:	learn: 0.0240288	total: 2h 5m 29s	remaining: 27m 47s
2456:	learn: 0.0240276	total: 2h 5m 33s	remaining: 27m 44s
2457:	learn: 0.0240093	total: 2h 5m 37s	remaining: 27m 41s
2458:	learn: 0.0240084	total: 2h 5m 40s	remaining: 27m 38s
2459:	learn: 0.0239850	total: 2h 5m 43s	remaining: 27m 35s
2460:	learn: 0.0239813	total: 2h 5m 46s	remaining: 27m 32s
2461:	learn: 0.0239776	total: 2h 5m 49s	remaining: 27m 29s
2462:	learn: 0.0239695	total: 2h 5m 53s	remaining: 27m 26s
246

2585:	learn: 0.0229041	total: 2h 12m 6s	remaining: 21m 8s
2586:	learn: 0.0228987	total: 2h 12m 8s	remaining: 21m 5s
2587:	learn: 0.0228956	total: 2h 12m 11s	remaining: 21m 2s
2588:	learn: 0.0228923	total: 2h 12m 14s	remaining: 20m 59s
2589:	learn: 0.0228825	total: 2h 12m 17s	remaining: 20m 56s
2590:	learn: 0.0228402	total: 2h 12m 19s	remaining: 20m 53s
2591:	learn: 0.0228206	total: 2h 12m 22s	remaining: 20m 50s
2592:	learn: 0.0228204	total: 2h 12m 26s	remaining: 20m 47s
2593:	learn: 0.0228194	total: 2h 12m 28s	remaining: 20m 44s
2594:	learn: 0.0227979	total: 2h 12m 31s	remaining: 20m 41s
2595:	learn: 0.0227961	total: 2h 12m 35s	remaining: 20m 38s
2596:	learn: 0.0227948	total: 2h 12m 38s	remaining: 20m 34s
2597:	learn: 0.0227930	total: 2h 12m 40s	remaining: 20m 31s
2598:	learn: 0.0227928	total: 2h 12m 43s	remaining: 20m 28s
2599:	learn: 0.0227921	total: 2h 12m 46s	remaining: 20m 25s
2600:	learn: 0.0227891	total: 2h 12m 49s	remaining: 20m 22s
2601:	learn: 0.0227877	total: 2h 12m 52s	rema

2723:	learn: 0.0217531	total: 2h 19m 14s	remaining: 14m 6s
2724:	learn: 0.0217487	total: 2h 19m 18s	remaining: 14m 3s
2725:	learn: 0.0217475	total: 2h 19m 21s	remaining: 14m
2726:	learn: 0.0217465	total: 2h 19m 24s	remaining: 13m 57s
2727:	learn: 0.0217361	total: 2h 19m 28s	remaining: 13m 54s
2728:	learn: 0.0217333	total: 2h 19m 31s	remaining: 13m 51s
2729:	learn: 0.0217315	total: 2h 19m 34s	remaining: 13m 48s
2730:	learn: 0.0217056	total: 2h 19m 38s	remaining: 13m 45s
2731:	learn: 0.0216959	total: 2h 19m 41s	remaining: 13m 42s
2732:	learn: 0.0216937	total: 2h 19m 44s	remaining: 13m 39s
2733:	learn: 0.0216929	total: 2h 19m 47s	remaining: 13m 36s
2734:	learn: 0.0216858	total: 2h 19m 50s	remaining: 13m 33s
2735:	learn: 0.0216714	total: 2h 19m 54s	remaining: 13m 29s
2736:	learn: 0.0216513	total: 2h 19m 58s	remaining: 13m 26s
2737:	learn: 0.0216510	total: 2h 20m 1s	remaining: 13m 23s
2738:	learn: 0.0216505	total: 2h 20m 4s	remaining: 13m 20s
2739:	learn: 0.0216496	total: 2h 20m 7s	remainin

2862:	learn: 0.0210834	total: 2h 26m 20s	remaining: 7m
2863:	learn: 0.0210824	total: 2h 26m 24s	remaining: 6m 57s
2864:	learn: 0.0210794	total: 2h 26m 27s	remaining: 6m 54s
2865:	learn: 0.0210789	total: 2h 26m 30s	remaining: 6m 51s
2866:	learn: 0.0210760	total: 2h 26m 33s	remaining: 6m 47s
2867:	learn: 0.0210733	total: 2h 26m 37s	remaining: 6m 44s
2868:	learn: 0.0210629	total: 2h 26m 40s	remaining: 6m 41s
2869:	learn: 0.0210622	total: 2h 26m 43s	remaining: 6m 38s
2870:	learn: 0.0210551	total: 2h 26m 47s	remaining: 6m 35s
2871:	learn: 0.0210449	total: 2h 26m 50s	remaining: 6m 32s
2872:	learn: 0.0210437	total: 2h 26m 53s	remaining: 6m 29s
2873:	learn: 0.0210420	total: 2h 26m 56s	remaining: 6m 26s
2874:	learn: 0.0210413	total: 2h 26m 59s	remaining: 6m 23s
2875:	learn: 0.0210380	total: 2h 27m 2s	remaining: 6m 20s
2876:	learn: 0.0210370	total: 2h 27m 6s	remaining: 6m 17s
2877:	learn: 0.0210356	total: 2h 27m 10s	remaining: 6m 14s
2878:	learn: 0.0210349	total: 2h 27m 13s	remaining: 6m 11s
287

Predict for model 7
Predict for model 8
Predict for model 9
Predict for model 10
Predict for model 11
Predict for model 12
Predict for model 13
Predict for model 14
Predict for model 15
Predict for model 16
Predict for model 17
Predict for model 18
Predict for model 19
Predict for model 20
Predict for model 21
Predict for model 22
Predict for model 23
Predict for model 24
Predict for model 25
Predict for model 26
Predict for model 27
Predict for model 28
Predict for model 29
Predict for model 30
Predict for model 31


In [24]:
pickle.dump(training_sets, open(DIRECTORY + 'training_sets_12_notebook.p', 'wb'))
pickle.dump((X_localtest, y_localtest, y_localtest_label), open(DIRECTORY + 'localtest_set_12_notebook.p', 'wb'))
pickle.dump((X_train, y_train), open(DIRECTORY + 'X_train_y_train_12_notebook.p', 'wb'))
pickle.dump(df, open(DIRECTORY + 'full_df_12_notebook.p', 'wb'))
pickle.dump(models, open(DIRECTORY + 'models_12_notebook.p', 'wb'))

In [ ]:
## After restarting notebook:

In [1]:
DIRECTORY = 'C:/Users/judit/Documents/learning/kaggle/Elo_201812/data/'

from catboost import CatBoostRegressor, CatBoostClassifier
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.utils import resample
from sklearn.metrics import mean_squared_error, accuracy_score, log_loss, confusion_matrix
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import pickle
import random
random.seed(1)

In [2]:
def make_list_of_predictions(models_list, test_set):
    predictions_class = []
    predictions_proba = []
    idx = 0
    for model in models_list:
        print('Predict for model', idx)
        prediction_class = model.predict(test_set)
        prediction_proba = model.predict_proba(test_set)
        predictions_class.append(prediction_class)
        predictions_proba.append(prediction_proba)
        idx += 1
    return predictions_class, predictions_proba

In [3]:
models = pickle.load(open(DIRECTORY + 'models_12_notebook.p', 'rb'))
(X_localtest, y_localtest, y_localtest_label) = pickle.load(open(DIRECTORY + 'localtest_set_12_notebook.p', 'rb'))

predictions_class, predictions_proba = make_list_of_predictions(models_list = models, test_set = X_localtest)
pickle.dump(predictions_class, open(DIRECTORY + 'predictions_class_12_notebook_1.p', 'wb'))
pickle.dump(predictions_proba, open(DIRECTORY + 'predictions_proba_12_notebook_1.p', 'wb'))

Predict for model 0
Predict for model 1
Predict for model 2
Predict for model 3
Predict for model 4
Predict for model 5
Predict for model 6
Predict for model 7
Predict for model 8
Predict for model 9
Predict for model 10
Predict for model 11
Predict for model 12
Predict for model 13
Predict for model 14
Predict for model 15
Predict for model 16
Predict for model 17
Predict for model 18
Predict for model 19
Predict for model 20
Predict for model 21
Predict for model 22
Predict for model 23
Predict for model 24
Predict for model 25
Predict for model 26
Predict for model 27
Predict for model 28
Predict for model 29
Predict for model 30
Predict for model 31
